## This notebook is to do missing data imputation

### Import Libraries

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

pd.set_option('display.max_rows',2000)
pd.set_option('display.max_columns',50)
pd.set_option('display.width',1000)

from pprint import pprint
from feature_engine import missing_data_imputers as mdi

import warnings
warnings.filterwarnings("ignore")

### Load Data and Split

In [2]:
df = pd.read_csv('test_values.csv')

In [3]:
df.head()

row_id county_code    state  population  renter_occupied_households  pct_renter_occupied  evictions  rent_burden  pct_white  pct_af_am  pct_hispanic  pct_am_ind  pct_asian  pct_nh_pi  pct_multiple  pct_other  poverty_rate                                               rucc                                    urban_influence                   economic_typology  pct_civilian_labor  pct_unemployment  pct_uninsured_adults  pct_uninsured_children  pct_adult_obesity  pct_adult_smoking  pct_diabetes  pct_low_birthweight  pct_excessive_drinking  pct_physical_inactivity  air_pollution_particulate_matter_value  homicides_per_100k  motor_vehicle_crash_deaths_per_100k  heart_disease_mortality_per_100k  pop_per_dentist  pop_per_primary_care_physician  pct_female  pct_below_18_years_of_age  pct_aged_65_years_and_older  pct_adults_less_than_a_high_school_diploma  pct_adults_with_high_school_diploma  pct_adults_with_some_college  pct_adults_bachelors_or_higher  birth_rate_per_1k  death_rate_per_1k
0       0     8e7613e  9d1e27d     52842.0                      5403.0               26.840        NaN       27.960   0.924234   0.025049      0.034351    0.001978   0.002308   0.000000      0.012080   0.000000        11.469  Metro - Counties in metro areas of fewer than ...  Small-in a metro area with fewer than 1 millio...                      Nonspecialized               0.436             0.075                 0.218                   0.057              0.284              0.257         0.114                0.080                   0.048                    0.332                               13.194028                3.31                                19.83                               293           4880.0                          2710.0       0.512                      0.215                        0.177                                    0.174651                             0.395210                      0.274451                        0.155689           9.828291          10.628268
1       1     694a5e8  a952566    212287.0                     53502.0               57.534     6032.0       33.072   0.398318   0.484635      0.063760    0.001394   0.021801   0.000199      0.028500   0.001394        19.170  Metro - Counties in metro areas of 1 million p...  Large-in a metro area with at least 1 million ...  Federal/State government-dependent               0.524             0.062                 0.225                   0.058              0.282              0.187         0.097                0.120                   0.164                    0.252                               12.419433               26.93                                10.83                               308            850.0                          1009.0       0.522                      0.192                        0.113                                    0.168327                             0.230080                      0.241036                        0.360558          13.285546           8.818293
2       2     b3f0726  20d32fc     81263.0                     13368.0               39.994     1012.0       32.044   0.483789   0.381916      0.099035    0.002509   0.009255   0.000800      0.018710   0.003988        17.408  Nonmetro - Urban population of 20,000 or more,...        Micropolitan adjacent to a large metro area             Manufacturing-dependent               0.464             0.094                 0.250                   0.081              0.349              0.121         0.137                0.099                     NaN                    0.308                               11.877446               10.26                                23.25                               269           2980.0                          2459.0       0.526                      0.240                        0.153                                    0.201816                             0.329970                      0.287588                        0.180626          11.571830          10.136089
3       3  

In [4]:
df.tail()

row_id county_code    state  population  renter_occupied_households  pct_renter_occupied  evictions  rent_burden  pct_white  pct_af_am  pct_hispanic  pct_am_ind  pct_asian  pct_nh_pi  pct_multiple  pct_other  poverty_rate                                               rucc                                    urban_influence economic_typology  pct_civilian_labor  pct_unemployment  pct_uninsured_adults  pct_uninsured_children  pct_adult_obesity  pct_adult_smoking  pct_diabetes  pct_low_birthweight  pct_excessive_drinking  pct_physical_inactivity  air_pollution_particulate_matter_value  homicides_per_100k  motor_vehicle_crash_deaths_per_100k  heart_disease_mortality_per_100k  pop_per_dentist  pop_per_primary_care_physician  pct_female  pct_below_18_years_of_age  pct_aged_65_years_and_older  pct_adults_less_than_a_high_school_diploma  pct_adults_with_high_school_diploma  pct_adults_with_some_college  pct_adults_bachelors_or_higher  birth_rate_per_1k  death_rate_per_1k
1571    1571     dae1584  52acab4     44414.0                      6275.0               35.026      254.0       30.569   0.726121   0.019125      0.054938    0.143854   0.005045   0.000301      0.050415   0.000201        13.606  Nonmetro - Urban population of 2,500 to 19,999...        Micropolitan adjacent to a small metro area    Nonspecialized               0.401             0.048                 0.300                   0.131              0.333              0.259         0.117                 0.08                   0.091                    0.297                               10.200021                5.67                                25.89                               330           2779.0                          2530.0       0.511                      0.233                        0.165                                    0.158683                             0.332335                      0.295409                        0.213573          13.675599          11.802539
1572    1572     b95e0ba  485e9af     16160.0                      1871.0               31.922        NaN       33.899   0.663196   0.303469      0.015262    0.001817   0.001717   0.000000      0.004257   0.010282        20.052  Nonmetro - Urban population of 2,500 to 19,999...  Noncore adjacent to a small metro with town of...    Nonspecialized               0.450             0.059                 0.254                   0.062              0.355              0.195         0.111                 0.10                     NaN                    0.333                               10.897362                 NaN                                30.34                               347           8620.0                          8160.0       0.495                      0.227                        0.176                                    0.210159                             0.419323                      0.240040                        0.130478          10.286142          13.278474
1573    1573     f44348c  1dcfd4e     28688.0                      4478.0               33.897        NaN       28.644   0.809853   0.011596      0.147624    0.001816   0.009389   0.003832      0.005427   0.010463         6.418  Nonmetro - Urban population of 20,000 or more,...          Micropolitan not adjacent to a metro area        Recreation               0.696             0.034                 0.231                   0.132              0.144              0.096         0.039                 0.11                   0.331                    0.117                               12.726635                 NaN                                10.74                                78           1229.0                           959.0       0.451                      0.170                        0.094                                    0.051793                             0.173307                      0.288845                        0.486056           9.229493           2.385150
1574    1574     c9450a6  52acab4     29234.0                      4528.0 

In [5]:
df.dtypes

row_id                                          int64
county_code                                    object
state                                          object
population                                    float64
renter_occupied_households                    float64
pct_renter_occupied                           float64
evictions                                     float64
rent_burden                                   float64
pct_white                                     float64
pct_af_am                                     float64
pct_hispanic                                  float64
pct_am_ind                                    float64
pct_asian                                     float64
pct_nh_pi                                     float64
pct_multiple                                  float64
pct_other                                     float64
poverty_rate                                  float64
rucc                                           object
urban_influence             

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1576 entries, 0 to 1575
Data columns (total 45 columns):
row_id                                        1576 non-null int64
county_code                                   1576 non-null object
state                                         1576 non-null object
population                                    1576 non-null float64
renter_occupied_households                    1576 non-null float64
pct_renter_occupied                           1576 non-null float64
evictions                                     1263 non-null float64
rent_burden                                   1576 non-null float64
pct_white                                     1576 non-null float64
pct_af_am                                     1576 non-null float64
pct_hispanic                                  1576 non-null float64
pct_am_ind                                    1576 non-null float64
pct_asian                                     1576 non-null float64
pct_nh_pi    

In [7]:
df.describe()

row_id    population  renter_occupied_households  pct_renter_occupied     evictions  rent_burden    pct_white    pct_af_am  pct_hispanic   pct_am_ind    pct_asian    pct_nh_pi  pct_multiple    pct_other  poverty_rate  pct_civilian_labor  pct_unemployment  pct_uninsured_adults  pct_uninsured_children  pct_adult_obesity  pct_adult_smoking  pct_diabetes  pct_low_birthweight  pct_excessive_drinking  pct_physical_inactivity  air_pollution_particulate_matter_value  homicides_per_100k  motor_vehicle_crash_deaths_per_100k  heart_disease_mortality_per_100k  pop_per_dentist  pop_per_primary_care_physician   pct_female  pct_below_18_years_of_age  pct_aged_65_years_and_older  pct_adults_less_than_a_high_school_diploma  pct_adults_with_high_school_diploma  pct_adults_with_some_college  pct_adults_bachelors_or_higher  birth_rate_per_1k  death_rate_per_1k
count  1576.000000  1.576000e+03                 1576.000000          1576.000000   1263.000000  1576.000000  1576.000000  1576.000000   1576.000000  1576.000000  1576.000000  1576.000000   1576.000000  1576.000000   1576.000000         1576.000000       1576.000000           1573.000000             1573.000000        1573.000000        1361.000000   1573.000000          1466.000000             1119.000000              1573.000000                             1563.000000          637.000000                          1399.000000                       1576.000000      1470.000000                     1485.000000  1573.000000                1573.000000                  1573.000000                                 1576.000000                          1576.000000                   1576.000000                     1576.000000        1576.000000        1576.000000
mean    787.500000  9.335925e+04                13026.646574            28.604343    330.127474    28.491293     0.777703     0.089202      0.084696     0.015787     0.012361     0.000833      0.018565     0.000852     12.223749            0.472693          0.062339              0.215020                0.085459           0.306643           0.213584      0.107628             0.083731                0.165150                 0.279910                               11.616655            5.794270                            21.381094                        278.209391      3517.072109                     2619.026263     0.500537                   0.228711                     0.167240                                    0.145707                             0.348718                      0.302235                        0.203340          11.750982          10.390796
std     455.096327  2.620079e+05                43974.207970             8.011919   1171.361516     4.464953     0.193223     0.144440      0.128088     0.064822     0.026029     0.004712      0.018096     0.001599      5.683836            0.074010          0.022760              0.064746                0.038708           0.041216           0.062011      0.022486             0.020926                0.051802                 0.052768                                1.527349            5.027517                            10.104331                         59.803588      2785.845176                     2312.952925     0.020815                   0.031792                     0.041578                                    0.065339                             0.070282                      0.051146                        0.088301           2.561985           2.792358
min       0.000000  1.170000e+02                   15.000000             9.159000     -1.000000    10.011000     0.063466     0.000000      0.000000     0.000000     0.000000     0.000000      0.000000     0.000000      0.000000            0.237000          0.013000              0.039000                0.013000           0.131000           0.066000      0.036000             0.040000                0.042000                 0.103000                                6.965724           -0.340000                             3.690000                     

In [8]:
df.shape

(1576, 45)

### Treat Missing Values using Feature-Engine

In [9]:
df.isnull().sum()

row_id                                          0
county_code                                     0
state                                           0
population                                      0
renter_occupied_households                      0
pct_renter_occupied                             0
evictions                                     313
rent_burden                                     0
pct_white                                       0
pct_af_am                                       0
pct_hispanic                                    0
pct_am_ind                                      0
pct_asian                                       0
pct_nh_pi                                       0
pct_multiple                                    0
pct_other                                       0
poverty_rate                                    0
rucc                                            0
urban_influence                                 0
economic_typology                               0


In [10]:
imputer = mdi.MeanMedianImputer(imputation_method='mean',variables=None)

In [11]:
imputer.fit(df)

MeanMedianImputer(imputation_method='mean',
                  variables=['row_id', 'population',
                             'renter_occupied_households',
                             'pct_renter_occupied', 'evictions', 'rent_burden',
                             'pct_white', 'pct_af_am', 'pct_hispanic',
                             'pct_am_ind', 'pct_asian', 'pct_nh_pi',
                             'pct_multiple', 'pct_other', 'poverty_rate',
                             'pct_civilian_labor', 'pct_unemployment',
                             'pct_uninsured_adults', 'pct_uninsured_children',
                             'pct_adult_obesity', 'pct_adult_smoking',
                             'pct_diabetes', 'pct_low_birthweight',
                             'pct_excessive_drinking',
                             'pct_physical_inactivity',
                             'air_pollution_particulate_matter_value',
                             'homicides_per_100k',
                            

In [12]:
df1 = imputer.transform(df)

In [13]:
df1.isnull().sum()

row_id                                        0
county_code                                   0
state                                         0
population                                    0
renter_occupied_households                    0
pct_renter_occupied                           0
evictions                                     0
rent_burden                                   0
pct_white                                     0
pct_af_am                                     0
pct_hispanic                                  0
pct_am_ind                                    0
pct_asian                                     0
pct_nh_pi                                     0
pct_multiple                                  0
pct_other                                     0
poverty_rate                                  0
rucc                                          0
urban_influence                               0
economic_typology                             0
pct_civilian_labor                      

In [14]:
df1

row_id county_code    state  population  renter_occupied_households  pct_renter_occupied     evictions  rent_burden  pct_white  pct_af_am  pct_hispanic  pct_am_ind  pct_asian  pct_nh_pi  pct_multiple  pct_other  poverty_rate                                               rucc                                    urban_influence                   economic_typology  pct_civilian_labor  pct_unemployment  pct_uninsured_adults  pct_uninsured_children  pct_adult_obesity  pct_adult_smoking  pct_diabetes  pct_low_birthweight  pct_excessive_drinking  pct_physical_inactivity  air_pollution_particulate_matter_value  homicides_per_100k  motor_vehicle_crash_deaths_per_100k  heart_disease_mortality_per_100k  pop_per_dentist  pop_per_primary_care_physician  pct_female  pct_below_18_years_of_age  pct_aged_65_years_and_older  pct_adults_less_than_a_high_school_diploma  pct_adults_with_high_school_diploma  pct_adults_with_some_college  pct_adults_bachelors_or_higher  birth_rate_per_1k  \
0          0     8e7613e  9d1e27d     52842.0                      5403.0               26.840    330.127474       27.960   0.924234   0.025049      0.034351    0.001978   0.002308   0.000000      0.012080   0.000000        11.469  Metro - Counties in metro areas of fewer than ...  Small-in a metro area with fewer than 1 millio...                      Nonspecialized               0.436             0.075               0.21800                0.057000           0.284000           0.257000      0.114000             0.080000                 0.04800                  0.33200                               13.194028             3.31000                            19.830000                               293      4880.000000                     2710.000000    0.512000                   0.215000                      0.17700                                    0.174651                             0.395210                      0.274451                        0.155689           9.828291   
1          1     694a5e8  a952566    212287.0                     53502.0               57.534   6032.000000       33.072   0.398318   0.484635      0.063760    0.001394   0.021801   0.000199      0.028500   0.001394        19.170  Metro - Counties in metro areas of 1 million p...  Large-in a metro area with at least 1 million ...  Federal/State government-dependent               0.524             0.062               0.22500                0.058000           0.282000           0.187000      0.097000             0.120000                 0.16400                  0.25200                               12.419433            26.93000                            10.830000                               308       850.000000                     1009.000000    0.522000                   0.192000                      0.11300                                    0.168327                             0.230080                      0.241036                        0.360558          13.285546   
2          2     b3f0726  20d32fc     81263.0                     13368.0               39.994   1012.000000       32.044   0.483789   0.381916      0.099035    0.002509   0.009255   0.000800      0.018710   0.003988        17.408  Nonmetro - Urban population of 20,000 or more,...        Micropolitan adjacent to a large metro area             Manufacturing-dependent               0.464             0.094               0.25000                0.081000           0.349000           0.121000      0.137000             0.099000                 0.16515                  0.30800                               11.877446            10.26000                            23.250000                               269      2980.000000                     2459.000000    0.526000                   0.240000                      0.15300                                    0.201816                             0.329970                      0.287588                        0.180626          11.571830   
3          3     fd922f0  1b0d913    122870.0         

In [15]:
df1.shape

(1576, 45)

### Save a copy

In [16]:
#df1.to_csv('testfilled.csv',index=False)